In [1]:
%load_ext autoreload
%autoreload 2

# Import necessary modules 
import numpy as np
import pandas as pd
from itertools import product
import plotly.graph_objs as go
import plotly.express as px
from numpy.linalg import eigvalsh
from plotly.subplots import make_subplots

from rbf_volatility_surface import RBFVolatilitySurface
from smoothness_prior import RBFQuadraticSmoothnessPrior
from dataset_sabr import generate_sabr_call_options

In [2]:
# Define the strike price list and maturity time list
strike_price_list = np.array([0.75, 0.85, 0.9, 0.95, 1.0, 1.05, 1.1, 1.2, 1.3, 1.5])
maturity_time_list = np.array([0.02, 0.08, 0.17, 0.25, 0.5, 0.75, 1.0, 1.5, 2.0, 3.0])

# Create the product grid of maturity times and strike prices
product_grid = list(product(maturity_time_list, strike_price_list))
maturity_times, strike_prices = zip(*product_grid)

# Convert to arrays for further operations
maturity_times = np.array(maturity_times)
strike_prices = np.array(strike_prices)

# Variance formula for log-uniform distribution
def log_uniform_variance(a, b):
    log_term = np.log(b / a)
    var = ((b ** 2 - a ** 2) / (2 * log_term)) - ((b - a) / log_term) ** 2
    return var

# Calculate standard deviations for maturity times and strike prices
maturity_std = np.sqrt(log_uniform_variance(maturity_time_list.min(), maturity_time_list.max()))
strike_std = np.sqrt(log_uniform_variance(strike_price_list.min(), strike_price_list.max()))

# Define the SABR model parameters
alpha = 0.20  # Stochastic volatility parameter
beta = 0.50   # Elasticity parameter
rho = -0.75   # Correlation between asset price and volatility
nu = 1.0      # Volatility of volatility parameter

# Other model parameters
risk_free_rate = np.log(1.02)  # Risk-free interest rate
underlying_price = 1.0         # Current price of the underlying asset

# Generate the dataset using the SABR model and Black-Scholes formula
call_option_dataset = generate_sabr_call_options(
    alpha=alpha,
    beta=beta,
    rho=rho,
    nu=nu,
    maturity_times=maturity_times,
    strike_prices=strike_prices,
    risk_free_rate=risk_free_rate,
    underlying_price=underlying_price
)

# Maturity times and strike prices from the previous product grid setup
hypothetical_maturity_time_list = np.logspace(np.log10(0.01), np.log10(3.1), 100)
hypothetical_strike_price_list = np.logspace(np.log10(0.7), np.log10(1.75), 100)

# Create the product grid of maturity times and strike prices
hypothetical_product_grid = list(product(hypothetical_maturity_time_list, hypothetical_strike_price_list))
hypothetical_maturity_times, hypothetical_strike_prices = zip(*hypothetical_product_grid)
hypothetical_maturity_times, hypothetical_strike_prices = np.array(hypothetical_maturity_times), np.array(hypothetical_strike_prices)

# Reshape the data for 3D surface plotting
hypothetical_maturities_grid = hypothetical_maturity_times.reshape((len(hypothetical_maturity_time_list), len(hypothetical_strike_price_list)))  
hypothetical_strikes_grid = hypothetical_strike_prices.reshape((len(hypothetical_maturity_time_list), len(hypothetical_strike_price_list)))

In [ ]:
n_roots = 350
smoothness_controller = 0.00001

# Initialize the RBFQuadraticSmoothnessPrior class
smoothness_prior = RBFQuadraticSmoothnessPrior(
    maturity_times=maturity_times,
    strike_prices=strike_prices,
    maturity_std=maturity_std,
    strike_std=strike_std,
    n_roots=n_roots,
    smoothness_controller=smoothness_controller,
    random_state=0,
)

In [44]:
# Generate 100 log-spaced values for the smoothness controller (gamma)
smoothness_values = np.logspace(-3, -1, 1000)

# Initialize a list to store log-likelihood values
log_likelihoods = []

# Loop through each smoothness value and calculate the log-likelihood
for gamma in smoothness_values:
    # Set the smoothness controller for the smoothness prior
    smoothness_prior.smoothness_controller = gamma
    
    # Calculate the log-likelihood for the current smoothness controller
    log_likelihood_value = smoothness_prior.log_likelihood(
        data_implied_volatilities=call_option_dataset["Implied Volatility"].values,
        data_maturity_times=call_option_dataset["Time to Maturity"].values,
        data_strike_prices=call_option_dataset["Strike Price"].values,
        risk_free_rate=risk_free_rate,
        underlying_price=underlying_price,
        noise_level=0
    )
    
    # Append the log-likelihood value to the list
    log_likelihoods.append(log_likelihood_value)

# Convert the list of log-likelihoods to a NumPy array for easy processing
log_likelihoods = np.array(log_likelihoods)

# Find the optimal smoothness controller (the one with the maximum log-likelihood)
optimal_smoothness = smoothness_values[np.argmax(log_likelihoods)]
smoothness_prior.smoothness_controller = optimal_smoothness

# Create a Plotly figure to visualize the log-likelihoods
fig = go.Figure()

# Add a line plot for the log-likelihood values
fig.add_trace(
    go.Scatter(
        x=smoothness_values,
        y=log_likelihoods,
        mode='lines+markers',
        name='Log-Likelihood',
        line=dict(color='royalblue', width=2),
        marker=dict(size=6)
    )
)

# Highlight the optimal smoothness controller with a vertical line
fig.add_trace(
    go.Scatter(
        x=[optimal_smoothness],
        y=[max(log_likelihoods)],
        mode='markers',
        name=f'Optimal γ: {optimal_smoothness:.4f}',
        marker=dict(color='red', size=10, symbol='circle')
    )
)

# Update the layout for the plot
fig.update_layout(
    title="Log-Likelihood vs Smoothness Controller",
    xaxis_title="Smoothness Controller (γ)",
    yaxis_title="Log-Likelihood",
    xaxis_type="log",  # Log scale for smoothness controller
    height=900,
    width=900
)

# Show the plot
fig.show()

# Print the optimal smoothness controller
print(f"Optimal smoothness controller: {optimal_smoothness}")

Optimal smoothness controller: 0.012679528467864345


In [32]:
n_roots = 350
smoothness_controller = 0.000028

# Initialize the RBFQuadraticSmoothnessPrior class
smoothness_prior = RBFQuadraticSmoothnessPrior(
    maturity_times=maturity_times,
    strike_prices=strike_prices,
    maturity_std=maturity_std,
    strike_std=strike_std,
    n_roots=n_roots,
    smoothness_controller=smoothness_controller,
    random_state=0,
)

In [33]:
# Calculate the prior covariance matrix
prior_covariance_matrix = smoothness_prior.prior_covariance()

# Display the covariance matrix
print("Prior Covariance Matrix:")
pd.DataFrame(prior_covariance_matrix)

Prior Covariance Matrix:


0             1             2             3             4   \
0   1.507892e-05 -6.063441e-05  4.945283e-05 -8.279976e-06 -3.861346e-06   
1  -6.063441e-05  4.452826e-04 -3.649597e-04  4.182490e-05  4.128912e-06   
2   4.945283e-05 -3.649597e-04  3.419037e-04 -4.986532e-05 -2.471247e-05   
3  -8.279976e-06  4.182490e-05 -4.986532e-05  1.428853e-04  3.160369e-06   
4  -3.861346e-06  4.128912e-06 -2.471247e-05  3.160369e-06  3.851305e-04   
..           ...           ...           ...           ...           ...   
95 -3.160204e-12  3.043986e-12  1.629532e-11  8.042228e-13 -2.065204e-11   
96 -1.092071e-12  5.705701e-12  3.555246e-13 -2.965689e-11 -4.019124e-12   
97 -8.989788e-14 -1.090323e-12  5.922739e-13  6.168823e-14  1.671109e-11   
98 -6.772277e-15  3.062308e-15 -1.126885e-15  7.720241e-15 -1.233996e-13   
99 -1.735048e-17  1.033270e-16  5.468905e-17 -5.595891e-16 -1.435368e-16   

              5             6             7             8             9   ...  \
0   3.026511e-06 -3.675269e-07  1.107157e-07 -4.431485e-09 -7.011288e-12  ...   
1  -2.130493e-05  2.106089e-06 -9.144627e-07  1.908200e-09  4.577445e-11  ...   
2  -2.559821e-06 -2.344339e-06 -7.675841e-08  4.198330e-09 -3.707824e-11  ...   
3  -2.722983e-06 -1.254729e-05 -8.762041e-08  3.666756e-09 -2.395871e-10  ...   
4  -4.419173e-06 -4.712720e-07  2.322032e-06 -1.745124e-08 -1.883659e-11  ...   
..           ...           ...           ...           ...           ...  ...   
95 -3.660345e-12 -1.809246e-12 -5.389645e-13 -2.845226e-14 -9.124496e-16  ...   
96 -1.809261e-12  2.187668e-11 -1.751415e-13 -9.390191e-15  4.266277e-16  ...   
97 -5.389538e-13 -1.751425e-13  2.001126e-13 -3.395172e-15  9.046279e-16  ...   
98 -2.845531e-14 -9.390099e-15 -3.393914e-15  1.013830e-15 -9.444172e-16  ...   
99 -9.203845e-16  4.207963e-16  9.024635e-16 -9.422359e-16  3.862696e-19  ...   

              90            91            92            93            94  \
0  -6.980639e-10 -1.745836e-10 -5.848903e-11 -2.399253e-11 -1.141767e-11   
1  -1.748511e-10  2.147924e-10  3.199302e-11  1.098885e-10  1.806786e-11   
2  -5.865539e-11  3.198084e-11  2.732092e-10  5.093437e-12  3.400341e-12   
3  -2.422178e-11  1.098750e-10  5.077383e-12 -5.730500e-10  8.302591e-12   
4  -1.149411e-11  1.803038e-11  3.413785e-12  8.294806e-12 -4.896894e-11   
..           ...           ...           ...           ...           ...   
95 -7.965854e-13 -6.075747e-13 -6.234642e-14 -8.306821e-14 -4.256365e-14   
96 -3.575827e-13 -4.721421e-14 -6.794636e-14 -3.623452e-14 -3.373538e-15   
97 -2.479270e-14 -2.176201e-14 -1.871451e-15 -2.801902e-15  8.939261e-17   
98 -3.293367e-15 -5.862094e-16 -7.808320e-18 -8.943968e-17 -7.530589e-16   
99  3.911447e-18  2.919540e-17 -1.248520e-16 -3.899781e-17 -1.556333e-17   

              95            96            97            98            99  
0  -3.160204e-12 -1.092071e-12 -8.989788e-14 -6.772277e-15 -1.735048e-17  
1   3.043986e-12  5.705701e-12 -1.090323e-12  3.062308e-15  1.033270e-16  
2   1.629532e-11  3.555246e-13  5.922739e-13 -1.126885e-15  5.468905e-17  
3   8.042228e-13 -2.965689e-11  6.168823e-14  7.720241e-15 -5.595891e-16  
4  -2.065204e-11 -4.019124e-12  1.671109e-11 -1.233996e-13 -1.435368e-16  
..           ...           ...           ...           ...           ...  
95  3.920000e-04 -3.953940e-15 -1.449566e-16  2.249033e-17  1.021516e-16  
96 -3.953940e-15  3.920000e-04  1.215008e-17  2.469973e-17 -3.621356e-17  
97 -1.449566e-16  1.215008e-17  3.920000e-04  1.182967e-17  7.126943e-16  
98  2.249033e-17  2.469973e-17  1.182967e-17  3.920000e-04 -7.759185e-17  
99  1.021516e-16 -3.621356e-17  7.126943e-16 -7.759185e-17  3.920000e-04  

[100 rows x 100 columns]

In [34]:
np.linalg.eigvalsh(prior_covariance_matrix)

array([3.70533874e-08, 2.39036027e-07, 6.87938630e-07, 4.62652911e-06,
       9.68881257e-06, 2.80556012e-05, 5.76796408e-05, 7.12434408e-05,
       1.34083642e-04, 1.93442676e-04, 2.06532028e-04, 2.98708186e-04,
       2.98855547e-04, 3.76311472e-04, 3.83282433e-04, 3.83704464e-04,
       3.88841016e-04, 3.89484265e-04, 3.90880270e-04, 3.91123189e-04,
       3.91328325e-04, 3.91779681e-04, 3.91840156e-04, 3.91874721e-04,
       3.91895785e-04, 3.91929448e-04, 3.91931008e-04, 3.91939046e-04,
       3.91963824e-04, 3.91991112e-04, 3.91995116e-04, 3.91997491e-04,
       3.91998414e-04, 3.91999008e-04, 3.91999385e-04, 3.91999869e-04,
       3.91999931e-04, 3.91999935e-04, 3.91999965e-04, 3.91999980e-04,
       3.91999988e-04, 3.91999993e-04, 3.91999996e-04, 3.91999998e-04,
       3.91999999e-04, 3.91999999e-04, 3.92000000e-04, 3.92000000e-04,
       3.92000000e-04, 3.92000000e-04, 3.92000000e-04, 3.92000000e-04,
       3.92000000e-04, 3.92000000e-04, 3.92000000e-04, 3.92000000e-04,
      

In [35]:
# Create a heatmap for the prior covariance matrix
fig1 = px.imshow(
    prior_covariance_matrix,
    labels=dict(x="Index", y="Index", color="Cov."),
    title="Smoothness Prior Covariance Matrix",
    color_continuous_scale="Viridis"
)

# Update layout for better visualization
fig1.update_layout(
    width=800,
    height=800,
    title_x=0.5,
    xaxis_title="Maturity and Strike Indices",
    yaxis_title="Maturity and Strike Indices",
)

# Show the figure
fig1.show()

In [36]:
# Compute the eigenvalues of the prior covariance matrix
eigenvalues = np.linalg.eigvalsh(prior_covariance_matrix)

# Sort eigenvalues by their absolute values in descending order
sorted_eigenvalues = np.sort(eigenvalues)[::-1]

# Calculate the cumulative explained variance
cumulative_explained_variance = np.cumsum(sorted_eigenvalues) / np.sum(sorted_eigenvalues)

# Create a bar plot for the sorted eigenvalues (original values) and a line plot for cumulative explained variance
fig2 = go.Figure()

# Bar plot for eigenvalues
fig2.add_trace(
    go.Bar(
        x=np.arange(1, len(sorted_eigenvalues) + 1),
        y=np.abs(sorted_eigenvalues),
        name="Eigenvalues",
    )
)

# Line plot for cumulative explained variance
fig2.add_trace(
    go.Scatter(
        x=np.arange(1, len(cumulative_explained_variance) + 1),
        y=cumulative_explained_variance,
        name="Cumulative Explained Variance",
        yaxis="y2",
        mode="lines",
    )
)

# Add figure layout
fig2.update_layout(
    title="Eigenvalues and Cumulative Explained Variance",
    xaxis=dict(title="Index of Eigenvalues"),
    yaxis=dict(title="Eigenvalues"),
    yaxis2=dict(
        title="Cumulative Explained Variance",
        overlaying="y",
        side="right",
        showgrid=False,
    ),
    width=900,
    height=900,
    title_x=0.5,
    legend=dict(x=0.1, y=0.9),
)

# Show the figure
fig2.show()

In [37]:
smoothness_prior.sample_smooth_surfaces(9)

array([[-1.36400116e-03,  1.11713068e-02, -9.34739337e-03,
         1.38069703e-02,  1.60810641e-03, -2.29787121e-02,
        -2.25528637e-02, -4.12851961e-02,  3.10738642e-04,
        -3.72139717e-03,  5.73595145e-04, -3.89119613e-03,
        -2.61854868e-03,  1.20670387e-02,  3.20707529e-02,
        -4.20034210e-02, -8.89465030e-03,  2.34829878e-02,
         9.27498238e-04,  2.81483590e-02, -2.86562069e-03,
         1.42304843e-02,  3.52279419e-03, -4.27770791e-02,
         1.34155019e-02, -1.43279946e-03,  1.51830163e-02,
         9.37873653e-03, -2.19125260e-02,  5.41611552e-03,
         6.75911324e-03, -2.03688395e-02,  9.49621223e-03,
        -2.07287586e-02,  9.22345854e-03, -4.86696096e-03,
        -1.60730630e-03,  3.70886182e-03,  4.89027624e-03,
        -4.85362684e-03, -3.63971750e-03, -9.63194588e-03,
         1.52407807e-03,  1.73694906e-02,  2.54687221e-02,
        -1.48934085e-02, -1.71447023e-02, -7.28945855e-03,
        -1.80574109e-02,  1.82136032e-02, -5.26958513e-0

In [38]:
# Sample 9 surface coefficients using the smoothness prior
n_samples = 9
sampled_coefficients = smoothness_prior.sample_smooth_surfaces(n_samples)

# The constant_volatility is set to a reasonable value
constant_volatility = RBFVolatilitySurface.calculate_constant_volatility(
    call_option_dataset["Implied Volatility"],
    call_option_dataset["Time to Maturity"],
    call_option_dataset["Strike Price"],
    risk_free_rate,
    underlying_price
)

# Create the 3x3 subplots
fig = make_subplots(
    rows=3, cols=3,
    subplot_titles=[f"Surface {i+1}" for i in range(n_samples)],
    specs=[[{'type': 'surface'}] * 3] * 3,
    vertical_spacing=0.05, horizontal_spacing=0.05
)

# Loop through the sampled coefficients to generate and plot each surface
for idx, coefficients in enumerate(sampled_coefficients):
    row = (idx // 3) + 1
    col = (idx % 3) + 1
    
    # Initialize the RBFVolatilitySurface class for each set of coefficients
    rbf_surface = RBFVolatilitySurface(
        coefficients=coefficients,
        maturity_times=maturity_times,
        strike_prices=strike_prices,
        maturity_std=maturity_std,
        strike_std=strike_std,
        constant_volatility=constant_volatility
    )

    # Generate the volatility surface over the product grid of times and strikes
    surface_volatilities = np.array([
        rbf_surface.implied_volatility_surface(T, K)
        for T, K in hypothetical_product_grid
    ]).reshape(len(hypothetical_maturity_time_list), len(hypothetical_strike_price_list))

    # Add the surface plot to the subplot
    fig.add_trace(
        go.Surface(
            x=hypothetical_strikes_grid,
            y=hypothetical_maturities_grid,
            z=surface_volatilities,
            showscale=False  # Hide the scale on individual plots
        ),
        row=row, col=col
    )

for i in range(1, 4):  # Rows
    for j in range(1, 4):  # Columns
        fig.update_scenes(
            dict(
                xaxis_title="Strike Price",
                yaxis_title="Time to Maturity",
                zaxis_title="Implied Volatility",
                aspectratio=dict(x=1, y=1, z=0.8)
            ),
            row=i, col=j
        )    

# Update the layout of the figure
fig.update_layout(
    title="Sampled Volatility Surfaces from Smoothness Prior",
    height=1500, width=1500,
)

# Show the plot
fig.show()